In [56]:
#importing the dependencies

import numpy as np
import pandas as pd
import math
import re
from scipy.sparse import csr_matrix
import matplotlib.pyplot as plt
import seaborn as sns
from surprise import Reader, Dataset, SVD
import difflib
from sklearn.feature_extraction.text import TfidfVectorizer #to convert textual data into vectors
from sklearn.metrics.pairwise import cosine_similarity
from surprise.model_selection.validation import cross_validate
sns.set_style("darkgrid")

In [57]:
#Data collection and preprocessing

#loading data from csv file into pandas data frame
#movies_data=drugs_data
drugs_data=pd.read_csv('webmd.csv')

In [58]:
drugs_data.head()

Age      Condition       Date                          Drug  DrugId  \
0  75 or over    Stuffy Nose  9/21/2014                  25dph-7.5peh  146724   
1       25-34  Cold Symptoms  1/13/2011                  25dph-7.5peh  146724   
2       65-74          Other  7/16/2012  warfarin (bulk) 100 % powder  144731   
3  75 or over          Other  9/23/2010  warfarin (bulk) 100 % powder  144731   
4       35-44          Other   1/6/2009  warfarin (bulk) 100 % powder  144731   

   EaseofUse  Effectiveness  \
0          5              5   
1          5              5   
2          2              3   
3          2              2   
4          1              1   

                                             Reviews  Satisfaction     Sex  \
0  I'm a retired physician and of all the meds I ...             5    Male   
1  cleared me right up even with my throat hurtin...             5  Female   
2  why did my PTINR go from a normal of 2.5 to ov...             3  Female   
3                       FALLING AND DON'T REALISE IT             1  Female   
4  My grandfather was prescribed this medication ...             1    Male   

                                               Sides  UsefulCount  
0  Drowsiness,  dizziness ,  dry mouth /nose/thro...            0  
1  Drowsiness,  dizziness ,  dry mouth /nose/thro...            1  
2                                                               0  
3                                                               0  
4                                                               1

In [59]:
#Number of rows and columns in the dataframe
drugs_data.shape

(362806, 12)

In [60]:
drugs_data['DrugId'].value_counts()

6873      8538
1025      7868
6007      7728
4398      5864
14208     5451
          ... 
4118         1
165948       1
54215        1
154021       1
149247       1
Name: DrugId, Length: 6572, dtype: int64

In [61]:
drugs_data['AvgRating'] = (drugs_data['EaseofUse'] + drugs_data['Effectiveness'] + drugs_data['Satisfaction'])/3
drugs_data.head()

Age      Condition       Date                          Drug  DrugId  \
0  75 or over    Stuffy Nose  9/21/2014                  25dph-7.5peh  146724   
1       25-34  Cold Symptoms  1/13/2011                  25dph-7.5peh  146724   
2       65-74          Other  7/16/2012  warfarin (bulk) 100 % powder  144731   
3  75 or over          Other  9/23/2010  warfarin (bulk) 100 % powder  144731   
4       35-44          Other   1/6/2009  warfarin (bulk) 100 % powder  144731   

   EaseofUse  Effectiveness  \
0          5              5   
1          5              5   
2          2              3   
3          2              2   
4          1              1   

                                             Reviews  Satisfaction     Sex  \
0  I'm a retired physician and of all the meds I ...             5    Male   
1  cleared me right up even with my throat hurtin...             5  Female   
2  why did my PTINR go from a normal of 2.5 to ov...             3  Female   
3                       FALLING AND DON'T REALISE IT             1  Female   
4  My grandfather was prescribed this medication ...             1    Male   

                                               Sides  UsefulCount  AvgRating  
0  Drowsiness,  dizziness ,  dry mouth /nose/thro...            0   5.000000  
1  Drowsiness,  dizziness ,  dry mouth /nose/thro...            1   5.000000  
2                                                               0   2.666667  
3                                                               0   1.666667  
4                                                               1   1.000000

In [62]:
drug_name=drugs_data.drop_duplicates(subset = "DrugId")
drug_name=drug_name[['DrugId','Drug','Condition']]
drug_name.head(10)

DrugId                                        Drug  \
0    146724                                25dph-7.5peh   
2    144731                warfarin (bulk) 100 % powder   
6    163180                                   wymzya fe   
9      9800     12 hour nasal relief spray, non-aerosol   
10    12112                         pyrogallol crystals   
11   164750                                        lyza   
30   149297                        lysiplex plus liquid   
31   154120                                     lysteda   
36   170586                     pyrithione zinc shampoo   
103  163405  lysine acetate 4,000 mg oral powder packet   

                            Condition  
0                         Stuffy Nose  
2                               Other  
6                       Birth Control  
9                         Stuffy Nose  
10                              Other  
11                      Birth Control  
30                              Other  
31   Abnormally Long or Heavy Periods  
36                           Dandruff  
103                             Other

In [63]:
print(type(drug_name))

<class 'pandas.core.frame.DataFrame'>


In [65]:
b=np.array([])
c=np.array([])
for idnew in drug_name['DrugId']:
    sum=0
    k=0
    for id,rate in zip(drugs_data['DrugId'],drugs_data['AvgRating']):
        if id==idnew:
            sum=sum+rate
            k=k+1
    sum=sum/k
    b=np.append(b,sum)
    c=np.append(c,k)
    print(b)
print("Finally Done !")

[5.]
[5.         2.33333333]
[5.         2.33333333 3.88888889]
[5.         2.33333333 3.88888889 2.66666667]
[5.         2.33333333 3.88888889 2.66666667 5.        ]
[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474]
[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.        ]
[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.         3.96078431]
[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.         3.96078431 2.33333333]
[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.         3.96078431 2.33333333 5.        ]
[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.         3.96078431 2.33333333 5.         4.72222222]
[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.         3.96078431 2.33333333 5.         4.72222222 1.33333333]
[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.         3.96078431 2.33333333 5.         4.722222

[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.         3.96078431 2.33333333 5.         4.72222222 1.33333333
 3.4273922  4.53333333 2.66666667 2.66666667 3.         5.
 3.23333333 3.22222222 1.66666667 3.41176471 3.33333333 5.
 3.66666667 3.66666667 3.97058824 2.49862259 4.54545455 4.35897436
 3.33333333 3.         3.71929825 1.33333333 3.54166667 3.91428571
 5.         3.56737589 3.25631769 2.98809524 1.66666667]
[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.         3.96078431 2.33333333 5.         4.72222222 1.33333333
 3.4273922  4.53333333 2.66666667 2.66666667 3.         5.
 3.23333333 3.22222222 1.66666667 3.41176471 3.33333333 5.
 3.66666667 3.66666667 3.97058824 2.49862259 4.54545455 4.35897436
 3.33333333 3.         3.71929825 1.33333333 3.54166667 3.91428571
 5.         3.56737589 3.25631769 2.98809524 1.66666667 4.07142857]
[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.         3.96078431 2.33333333 5.

[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.         3.96078431 2.33333333 5.         4.72222222 1.33333333
 3.4273922  4.53333333 2.66666667 2.66666667 3.         5.
 3.23333333 3.22222222 1.66666667 3.41176471 3.33333333 5.
 3.66666667 3.66666667 3.97058824 2.49862259 4.54545455 4.35897436
 3.33333333 3.         3.71929825 1.33333333 3.54166667 3.91428571
 5.         3.56737589 3.25631769 2.98809524 1.66666667 4.07142857
 3.33333333 4.56451613 4.         2.33333333 3.8125     3.84202899
 4.33333333 4.12121212 3.38888889 3.99047619 3.35714286 3.08139535
 3.38202247 3.17753623 3.21461187]
[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.         3.96078431 2.33333333 5.         4.72222222 1.33333333
 3.4273922  4.53333333 2.66666667 2.66666667 3.         5.
 3.23333333 3.22222222 1.66666667 3.41176471 3.33333333 5.
 3.66666667 3.66666667 3.97058824 2.49862259 4.54545455 4.35897436
 3.33333333 3.         3.71929825 1.33333333 3.54166667 3.9

[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.         3.96078431 2.33333333 5.         4.72222222 1.33333333
 3.4273922  4.53333333 2.66666667 2.66666667 3.         5.
 3.23333333 3.22222222 1.66666667 3.41176471 3.33333333 5.
 3.66666667 3.66666667 3.97058824 2.49862259 4.54545455 4.35897436
 3.33333333 3.         3.71929825 1.33333333 3.54166667 3.91428571
 5.         3.56737589 3.25631769 2.98809524 1.66666667 4.07142857
 3.33333333 4.56451613 4.         2.33333333 3.8125     3.84202899
 4.33333333 4.12121212 3.38888889 3.99047619 3.35714286 3.08139535
 3.38202247 3.17753623 3.21461187 3.46464646 4.33333333 2.88888889
 3.875      4.66666667 3.98550725 3.98791873 4.0952381  3.44444444
 2.         4.16666667 2.88888889]
[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.         3.96078431 2.33333333 5.         4.72222222 1.33333333
 3.4273922  4.53333333 2.66666667 2.66666667 3.         5.
 3.23333333 3.22222222 1.66666667 3.41176471 3.3333

[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.         3.96078431 2.33333333 5.         4.72222222 1.33333333
 3.4273922  4.53333333 2.66666667 2.66666667 3.         5.
 3.23333333 3.22222222 1.66666667 3.41176471 3.33333333 5.
 3.66666667 3.66666667 3.97058824 2.49862259 4.54545455 4.35897436
 3.33333333 3.         3.71929825 1.33333333 3.54166667 3.91428571
 5.         3.56737589 3.25631769 2.98809524 1.66666667 4.07142857
 3.33333333 4.56451613 4.         2.33333333 3.8125     3.84202899
 4.33333333 4.12121212 3.38888889 3.99047619 3.35714286 3.08139535
 3.38202247 3.17753623 3.21461187 3.46464646 4.33333333 2.88888889
 3.875      4.66666667 3.98550725 3.98791873 4.0952381  3.44444444
 2.         4.16666667 2.88888889 3.64724919 4.         4.5
 5.         3.66666667 4.         4.625      4.         3.16666667
 3.50318471 3.04477612 3.66666667 4.57142857]
[5.         2.33333333 3.88888889 2.66666667 5.         3.15789474
 1.         3.96078431 2.33333333 5.   

...

[5.         2.33333333 3.88888889 ... 3.360587   2.         3.8125    ]
[5.         2.33333333 3.88888889 ... 2.         3.8125     3.09      ]
[5.         2.33333333 3.88888889 ... 3.8125     3.09       4.        ]
[5.         2.33333333 3.88888889 ... 3.09       4.         3.30894309]
[5.         2.33333333 3.88888889 ... 4.         3.30894309 3.88888889]
[5.         2.33333333 3.88888889 ... 3.30894309 3.88888889 5.        ]
[5.         2.33333333 3.88888889 ... 3.88888889 5.         3.        ]
[5.         2.33333333 3.88888889 ... 5.         3.         3.75757576]
[5.         2.33333333 3.88888889 ... 3.         3.75757576 3.75959596]
[5.         2.33333333 3.88888889 ... 3.75757576 3.75959596 3.92857143]
[5.         2.33333333 3.88888889 ... 3.75959596 3.92857143 5.        ]
[5.         2.33333333 3.88888889 ... 3.92857143 5.         4.41666667]
[5.         2.33333333 3.88888889 ... 5.         4.41666667 3.83333333]
[5.         2.33333333 3.88888889 ... 4.41666667 3.83333333 3.15

[5.         2.33333333 3.88888889 ... 1.         5.         3.        ]
[5.         2.33333333 3.88888889 ... 5.         3.         2.44444444]
[5.         2.33333333 3.88888889 ... 3.         2.44444444 4.20833333]
[5.         2.33333333 3.88888889 ... 2.44444444 4.20833333 4.66666667]
[5.         2.33333333 3.88888889 ... 4.20833333 4.66666667 3.2       ]
[5.         2.33333333 3.88888889 ... 4.66666667 3.2        3.87719298]
[5.         2.33333333 3.88888889 ... 3.2        3.87719298 2.44444444]
[5.         2.33333333 3.88888889 ... 3.87719298 2.44444444 1.66666667]
[5.         2.33333333 3.88888889 ... 2.44444444 1.66666667 4.22222222]
[5.         2.33333333 3.88888889 ... 1.66666667 4.22222222 5.        ]
[5.         2.33333333 3.88888889 ... 4.22222222 5.         3.66666667]
[5.         2.33333333 3.88888889 ... 5.         3.66666667 1.66666667]
[5.         2.33333333 3.88888889 ... 3.66666667 1.66666667 5.        ]
[5.         2.33333333 3.88888889 ... 1.66666667 5.         5.  

[5.         2.33333333 3.88888889 ... 3.9047619  4.41666667 5.        ]
[5.         2.33333333 3.88888889 ... 4.41666667 5.         3.74637681]
[5.         2.33333333 3.88888889 ... 5.         3.74637681 1.66666667]
[5.         2.33333333 3.88888889 ... 3.74637681 1.66666667 3.45833333]
[5.         2.33333333 3.88888889 ... 1.66666667 3.45833333 3.51207729]
[5.         2.33333333 3.88888889 ... 3.45833333 3.51207729 3.8125    ]
[5.         2.33333333 3.88888889 ... 3.51207729 3.8125     3.        ]
[5.         2.33333333 3.88888889 ... 3.8125     3.         1.66666667]
[5.         2.33333333 3.88888889 ... 3.         1.66666667 3.        ]
[5.         2.33333333 3.88888889 ... 1.66666667 3.         3.66666667]
[5.         2.33333333 3.88888889 ... 3.         3.66666667 2.66666667]
[5.         2.33333333 3.88888889 ... 3.66666667 2.66666667 4.48333333]
[5.         2.33333333 3.88888889 ... 2.66666667 4.48333333 1.        ]
[5.         2.33333333 3.88888889 ... 4.48333333 1.         2.91

[5.         2.33333333 3.88888889 ... 3.66666667 3.46666667 5.        ]
[5.         2.33333333 3.88888889 ... 3.46666667 5.         4.55555556]
[5.         2.33333333 3.88888889 ... 5.         4.55555556 5.        ]
[5.         2.33333333 3.88888889 ... 4.55555556 5.         2.        ]
[5.         2.33333333 3.88888889 ... 5.         2.         5.        ]
[5.         2.33333333 3.88888889 ... 2.         5.         4.33333333]
[5.         2.33333333 3.88888889 ... 5.         4.33333333 4.36666667]
[5.         2.33333333 3.88888889 ... 4.33333333 4.36666667 1.33333333]
[5.         2.33333333 3.88888889 ... 4.36666667 1.33333333 3.66666667]
[5.         2.33333333 3.88888889 ... 1.33333333 3.66666667 3.91666667]
[5.         2.33333333 3.88888889 ... 3.66666667 3.91666667 3.33333333]
[5.         2.33333333 3.88888889 ... 3.91666667 3.33333333 5.        ]
[5.         2.33333333 3.88888889 ... 3.33333333 5.         3.33333333]
[5.         2.33333333 3.88888889 ... 5.         3.33333333 2.44

[5.         2.33333333 3.88888889 ... 4.16666667 3.66666667 2.66666667]
[5.         2.33333333 3.88888889 ... 3.66666667 2.66666667 3.57142857]
[5.         2.33333333 3.88888889 ... 2.66666667 3.57142857 2.83333333]
[5.         2.33333333 3.88888889 ... 3.57142857 2.83333333 2.33333333]
[5.         2.33333333 3.88888889 ... 2.83333333 2.33333333 4.        ]
[5.         2.33333333 3.88888889 ... 2.33333333 4.         4.66666667]
[5.         2.33333333 3.88888889 ... 4.         4.66666667 3.22222222]
[5.         2.33333333 3.88888889 ... 4.66666667 3.22222222 3.33333333]
[5.         2.33333333 3.88888889 ... 3.22222222 3.33333333 4.77777778]
[5.         2.33333333 3.88888889 ... 3.33333333 4.77777778 4.66666667]
[5.         2.33333333 3.88888889 ... 4.77777778 4.66666667 2.13333333]
[5.         2.33333333 3.88888889 ... 4.66666667 2.13333333 1.        ]
[5.         2.33333333 3.88888889 ... 2.13333333 1.         3.76190476]
[5.         2.33333333 3.88888889 ... 1.         3.76190476 3.68

In [66]:
df1=pd.DataFrame({"Ratings":b})
df1.head(10)

Ratings
0  5.000000
1  2.333333
2  3.888889
3  2.666667
4  5.000000
5  3.157895
6  1.000000
7  3.960784
8  2.333333
9  5.000000

In [67]:
df2=pd.DataFrame({"NoOfReviews":c})
df2.head(10)

NoOfReviews
0         54.0
1          4.0
2          3.0
3         27.0
4          1.0
5         19.0
6          1.0
7        136.0
8          2.0
9          1.0

In [68]:
drug_name=pd.concat([drug_name,df1,df2],axis=1)

In [69]:
drug_name.head(10)

DrugId                                        Drug  \
0    146724.0                                25dph-7.5peh   
2    144731.0                warfarin (bulk) 100 % powder   
6    163180.0                                   wymzya fe   
9      9800.0     12 hour nasal relief spray, non-aerosol   
10    12112.0                         pyrogallol crystals   
11   164750.0                                        lyza   
30   149297.0                        lysiplex plus liquid   
31   154120.0                                     lysteda   
36   170586.0                     pyrithione zinc shampoo   
103  163405.0  lysine acetate 4,000 mg oral powder packet   

                            Condition   Ratings  NoOfReviews  
0                         Stuffy Nose  5.000000         54.0  
2                               Other  3.888889          3.0  
6                       Birth Control  1.000000          1.0  
9                         Stuffy Nose  5.000000          1.0  
10                              Other  4.722222         12.0  
11                      Birth Control  1.333333          2.0  
30                              Other  3.333333          1.0  
31   Abnormally Long or Heavy Periods  3.000000          1.0  
36                           Dandruff  5.000000          1.0  
103                             Other  3.031250        192.0

In [70]:
drug_name['index'] = np.arange(len(drug_name))

In [84]:
drug_name.head(12)

DrugId                                        Drug  \
0    146724.0                                25dph-7.5peh   
2    144731.0                warfarin (bulk) 100 % powder   
6    163180.0                                   wymzya fe   
9      9800.0     12 hour nasal relief spray, non-aerosol   
10    12112.0                         pyrogallol crystals   
11   164750.0                                        lyza   
30   149297.0                        lysiplex plus liquid   
31   154120.0                                     lysteda   
36   170586.0                     pyrithione zinc shampoo   
103  163405.0  lysine acetate 4,000 mg oral powder packet   
120  167493.0                             lynparza tablet   
182   75352.0                            lymphazurin vial   

                                             Condition   Ratings  NoOfReviews  \
0                                          Stuffy Nose  5.000000         54.0   
2                                                Other  3.888889          3.0   
6                                        Birth Control  1.000000          1.0   
9                                          Stuffy Nose  5.000000          1.0   
10                                               Other  4.722222         12.0   
11                                       Birth Control  1.333333          2.0   
30                                               Other  3.333333          1.0   
31                    Abnormally Long or Heavy Periods  3.000000          1.0   
36                                            Dandruff  5.000000          1.0   
103                                              Other  3.031250        192.0   
120  Cancer of Ovary in Patient with Germline BRCA ...  2.166667          2.0   
182                                              Other  2.666667          4.0   

     index  
0        0  
2        1  
6        2  
9        3  
10       4  
11       5  
30       6  
31       7  
36       8  
103      9  
120     10  
182     11

In [ ]:
# determining the name of the file 
file_name = 'concise_data.xlsx'
  
# saving the excel 
drug_name.to_excel(file_name) 
print('DataFrame is written to Excel File successfully.')

In [ ]:
drugs_name=pd.read_excel('concise_data.xlsx')